CatBoost - Продвинутая библиотека градиентного бустинга на деревьях решений с открытым исходным кодом.

Заявляется, что хорошо относится к категориальным признакам и не требует их предварительной обработки.

In [1]:
# !pip install catboost

In [2]:
# !pip install ipywidgets

In [3]:
import pandas as pd
import numpy as np

from catboost import Pool, CatBoostRegressor

from sklearn.model_selection import train_test_split

# Загружаем данные

In [14]:
X = pd.read_csv('EDAv2_Train.zip').drop(columns='price').drop(columns='description')
y = pd.read_csv('EDAv2_Train.zip', usecols=['price'])

X_test = pd.read_csv('EDAv2_Test.zip').drop(columns='description')

In [15]:
# категориальные признаки
cat_features_list = ['body_type', 'brand', 'color', 'fuel_type', 'n_doors', 
                     'vehicle_transmission', 'drive_type', 'n_owners', 
                     'is_original_techpass', 'is_lefthand_drive', 'full_model_name']
# текстовые признаки - оказывается, что только для классификатора
# text_features_list = ['description']
# X[text_features_list] = X[text_features_list].fillna(value='')

In [16]:
# оставим в тренировочном датасете только те бренды, которые есть в тестовом
brand_list = list(X_test['brand'].unique())
brand_mask = X['brand'].apply(lambda x: True if x in brand_list else False)
X = X[brand_mask]
y = y[brand_mask]
print(X.shape)

(47453, 16)


In [18]:
# оставим в тренировочном датасете только б/у машины
used_cars_mask = list(X['n_owners'] != '0')
X = X[used_cars_mask]
y = y[used_cars_mask]
print(X.shape)

(37841, 16)


In [19]:
# посмотрим сколько уникальных значений по кат-признакам
X.append(X_test)[cat_features_list].nunique()
# full_model_name точно будет слишком накладно делать one-hot, остальное можно проверить

body_type                12
brand                    12
color                    11
fuel_type                 5
n_doors                   5
vehicle_transmission      4
drive_type                3
n_owners                  3
is_original_techpass      2
is_lefthand_drive         2
full_model_name         572
dtype: int64

In [20]:
# разделим на обучающую и валидационную
test_size = 0.2
seed = 73
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=test_size, random_state=seed)
print(X_train.shape, y_train.shape)
print(X_valid.shape, y_valid.shape)

(30272, 16) (30272, 1)
(7569, 16) (7569, 1)


In [23]:
# готовим для CatBoost
train_pool = Pool(X_train, y_train, cat_features=cat_features_list)
valid_pool = Pool(X_valid, y_valid, cat_features=cat_features_list)
full_pool = Pool(X, y, cat_features=cat_features_list)

In [26]:
# готовим тюнинг гиперпараметров по сетке #1
model_grid = CatBoostRegressor(iterations=1000, 
                               loss_function='MAE', 
                               eval_metric='MAPE',
                               logging_level='Silent')
grid = {'depth': [4, 6, 8],
        'rsm': [0.5, 0.75, 1.0],
        'one_hot_max_size': [2, 5, 12],
        'random_strength': [1, 2]}
# grid_search_result = model_grid.grid_search(grid,
#                                             full_pool,
#                                             cv=3,
#                                             plot=True)

Custom logger is already specified. Specify more than one logger at same time is not thread safe.

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 0.9540229	test: 0.9526969	best: 0.9526969 (0)	total: 10.1ms	remaining: 10.1s
1:	learn: 0.9140201	test: 0.9119425	best: 0.9119425 (1)	total: 55ms	remaining: 27.4s
2:	learn: 0.8763273	test: 0.8736824	best: 0.8736824 (2)	total: 93.3ms	remaining: 31s
3:	learn: 0.8424117	test: 0.8396608	best: 0.8396608 (3)	total: 126ms	remaining: 31.4s
4:	learn: 0.8088609	test: 0.8058626	best: 0.8058626 (4)	total: 137ms	remaining: 27.3s
5:	learn: 0.7821750	test: 0.7794309	best: 0.7794309 (5)	total: 167ms	remaining: 27.7s
6:	learn: 0.7553474	test: 0.7533142	best: 0.7533142 (6)	total: 182ms	remaining: 25.8s
7:	learn: 0.7314251	test: 0.7300085	best: 0.7300085 (7)	total: 206ms	remaining: 25.6s
8:	learn: 0.7067522	test: 0.7056352	best: 0.7056352 (8)	total: 232ms	remaining: 25.6s
9:	learn: 0.6830874	test: 0.6824434	best: 0.6824434 (9)	total: 258ms	remaining: 25.5s
10:	learn: 0.6600568	test: 0.6598692	best: 0.6598692 (10)	total: 281ms	remaining: 25.2s
11:	learn: 0.6388950	test: 0.6391248	best: 0.6391248 

100:	learn: 0.2179664	test: 0.2219895	best: 0.2219895 (100)	total: 2.56s	remaining: 22.8s
101:	learn: 0.2174023	test: 0.2214057	best: 0.2214057 (101)	total: 2.59s	remaining: 22.8s
102:	learn: 0.2172081	test: 0.2212013	best: 0.2212013 (102)	total: 2.62s	remaining: 22.8s
103:	learn: 0.2169471	test: 0.2209546	best: 0.2209546 (103)	total: 2.64s	remaining: 22.8s
104:	learn: 0.2162907	test: 0.2202908	best: 0.2202908 (104)	total: 2.66s	remaining: 22.7s
105:	learn: 0.2159361	test: 0.2199262	best: 0.2199262 (105)	total: 2.69s	remaining: 22.7s
106:	learn: 0.2155041	test: 0.2195168	best: 0.2195168 (106)	total: 2.71s	remaining: 22.6s
107:	learn: 0.2151434	test: 0.2191381	best: 0.2191381 (107)	total: 2.74s	remaining: 22.6s
108:	learn: 0.2147069	test: 0.2185022	best: 0.2185022 (108)	total: 2.76s	remaining: 22.6s
109:	learn: 0.2142381	test: 0.2179898	best: 0.2179898 (109)	total: 2.79s	remaining: 22.6s
110:	learn: 0.2136867	test: 0.2173470	best: 0.2173470 (110)	total: 2.82s	remaining: 22.6s
111:	learn

196:	learn: 0.1953563	test: 0.1980012	best: 0.1979975 (195)	total: 5.04s	remaining: 20.6s
197:	learn: 0.1952172	test: 0.1978702	best: 0.1978702 (197)	total: 5.07s	remaining: 20.5s
198:	learn: 0.1950837	test: 0.1977223	best: 0.1977223 (198)	total: 5.09s	remaining: 20.5s
199:	learn: 0.1950040	test: 0.1976493	best: 0.1976493 (199)	total: 5.12s	remaining: 20.5s
200:	learn: 0.1948493	test: 0.1974910	best: 0.1974910 (200)	total: 5.14s	remaining: 20.4s
201:	learn: 0.1947554	test: 0.1974009	best: 0.1974009 (201)	total: 5.16s	remaining: 20.4s
202:	learn: 0.1946730	test: 0.1972270	best: 0.1972270 (202)	total: 5.19s	remaining: 20.4s
203:	learn: 0.1945635	test: 0.1971461	best: 0.1971461 (203)	total: 5.21s	remaining: 20.3s
204:	learn: 0.1944179	test: 0.1969635	best: 0.1969635 (204)	total: 5.24s	remaining: 20.3s
205:	learn: 0.1942909	test: 0.1968437	best: 0.1968437 (205)	total: 5.26s	remaining: 20.3s
206:	learn: 0.1942053	test: 0.1967628	best: 0.1967628 (206)	total: 5.29s	remaining: 20.3s
207:	learn

...

536:	learn: 0.1411541	test: 0.1568471	best: 0.1568471 (536)	total: 15.1s	remaining: 13s
537:	learn: 0.1410959	test: 0.1568295	best: 0.1568295 (537)	total: 15.1s	remaining: 13s
538:	learn: 0.1410510	test: 0.1567921	best: 0.1567921 (538)	total: 15.2s	remaining: 13s
539:	learn: 0.1410037	test: 0.1567631	best: 0.1567631 (539)	total: 15.2s	remaining: 12.9s
540:	learn: 0.1409275	test: 0.1567137	best: 0.1567137 (540)	total: 15.2s	remaining: 12.9s
541:	learn: 0.1408739	test: 0.1566748	best: 0.1566748 (541)	total: 15.2s	remaining: 12.9s
542:	learn: 0.1407865	test: 0.1566396	best: 0.1566396 (542)	total: 15.3s	remaining: 12.8s
543:	learn: 0.1407110	test: 0.1566219	best: 0.1566219 (543)	total: 15.3s	remaining: 12.8s
544:	learn: 0.1406512	test: 0.1565791	best: 0.1565791 (544)	total: 15.3s	remaining: 12.8s
545:	learn: 0.1406160	test: 0.1565599	best: 0.1565599 (545)	total: 15.4s	remaining: 12.8s
546:	learn: 0.1405267	test: 0.1565139	best: 0.1565139 (546)	total: 15.4s	remaining: 12.7s
547:	learn: 0.14

628:	learn: 0.1365428	test: 0.1545242	best: 0.1545242 (628)	total: 17.8s	remaining: 10.5s
629:	learn: 0.1365213	test: 0.1545059	best: 0.1545059 (629)	total: 17.8s	remaining: 10.5s
630:	learn: 0.1364764	test: 0.1544691	best: 0.1544691 (630)	total: 17.8s	remaining: 10.4s
631:	learn: 0.1364223	test: 0.1544193	best: 0.1544193 (631)	total: 17.9s	remaining: 10.4s
632:	learn: 0.1363787	test: 0.1544176	best: 0.1544176 (632)	total: 17.9s	remaining: 10.4s
633:	learn: 0.1363424	test: 0.1544059	best: 0.1544059 (633)	total: 17.9s	remaining: 10.3s
634:	learn: 0.1362885	test: 0.1543651	best: 0.1543651 (634)	total: 17.9s	remaining: 10.3s
635:	learn: 0.1362502	test: 0.1543481	best: 0.1543481 (635)	total: 18s	remaining: 10.3s
636:	learn: 0.1361951	test: 0.1543399	best: 0.1543399 (636)	total: 18s	remaining: 10.2s
637:	learn: 0.1361663	test: 0.1543135	best: 0.1543135 (637)	total: 18s	remaining: 10.2s
638:	learn: 0.1361173	test: 0.1542802	best: 0.1542802 (638)	total: 18s	remaining: 10.2s
639:	learn: 0.1360

724:	learn: 0.1324493	test: 0.1532039	best: 0.1532039 (724)	total: 20.4s	remaining: 7.74s
725:	learn: 0.1323885	test: 0.1531561	best: 0.1531561 (725)	total: 20.4s	remaining: 7.72s
726:	learn: 0.1323451	test: 0.1531549	best: 0.1531549 (726)	total: 20.5s	remaining: 7.69s
727:	learn: 0.1323254	test: 0.1531360	best: 0.1531360 (727)	total: 20.5s	remaining: 7.66s
728:	learn: 0.1322900	test: 0.1531155	best: 0.1531155 (728)	total: 20.5s	remaining: 7.63s
729:	learn: 0.1322484	test: 0.1531000	best: 0.1531000 (729)	total: 20.5s	remaining: 7.6s
730:	learn: 0.1322221	test: 0.1531019	best: 0.1531000 (729)	total: 20.6s	remaining: 7.57s
731:	learn: 0.1321780	test: 0.1530719	best: 0.1530719 (731)	total: 20.6s	remaining: 7.54s
732:	learn: 0.1321352	test: 0.1530580	best: 0.1530580 (732)	total: 20.6s	remaining: 7.52s
733:	learn: 0.1320923	test: 0.1530462	best: 0.1530462 (733)	total: 20.7s	remaining: 7.5s
734:	learn: 0.1320403	test: 0.1530351	best: 0.1530351 (734)	total: 20.7s	remaining: 7.47s
735:	learn: 

816:	learn: 0.1293876	test: 0.1521704	best: 0.1521704 (816)	total: 23.1s	remaining: 5.18s
817:	learn: 0.1293545	test: 0.1521571	best: 0.1521571 (817)	total: 23.2s	remaining: 5.15s
818:	learn: 0.1293299	test: 0.1521406	best: 0.1521406 (818)	total: 23.2s	remaining: 5.12s
819:	learn: 0.1293197	test: 0.1521616	best: 0.1521406 (818)	total: 23.2s	remaining: 5.1s
820:	learn: 0.1292906	test: 0.1521534	best: 0.1521406 (818)	total: 23.2s	remaining: 5.07s
821:	learn: 0.1292565	test: 0.1521488	best: 0.1521406 (818)	total: 23.3s	remaining: 5.04s
822:	learn: 0.1292317	test: 0.1521179	best: 0.1521179 (822)	total: 23.3s	remaining: 5.01s
823:	learn: 0.1291959	test: 0.1520934	best: 0.1520934 (823)	total: 23.3s	remaining: 4.98s
824:	learn: 0.1291619	test: 0.1520833	best: 0.1520833 (824)	total: 23.4s	remaining: 4.95s
825:	learn: 0.1291403	test: 0.1520978	best: 0.1520833 (824)	total: 23.4s	remaining: 4.92s
826:	learn: 0.1291168	test: 0.1520843	best: 0.1520833 (824)	total: 23.4s	remaining: 4.9s
827:	learn: 

911:	learn: 0.1266098	test: 0.1512728	best: 0.1512368 (907)	total: 25.8s	remaining: 2.49s
912:	learn: 0.1265783	test: 0.1512594	best: 0.1512368 (907)	total: 25.9s	remaining: 2.46s
913:	learn: 0.1265544	test: 0.1512499	best: 0.1512368 (907)	total: 25.9s	remaining: 2.44s
914:	learn: 0.1265225	test: 0.1512430	best: 0.1512368 (907)	total: 25.9s	remaining: 2.41s
915:	learn: 0.1264997	test: 0.1512379	best: 0.1512368 (907)	total: 25.9s	remaining: 2.38s
916:	learn: 0.1264374	test: 0.1512180	best: 0.1512180 (916)	total: 26s	remaining: 2.35s
917:	learn: 0.1263818	test: 0.1512036	best: 0.1512036 (917)	total: 26s	remaining: 2.32s
918:	learn: 0.1263625	test: 0.1511941	best: 0.1511941 (918)	total: 26s	remaining: 2.29s
919:	learn: 0.1263013	test: 0.1511629	best: 0.1511629 (919)	total: 26.1s	remaining: 2.27s
920:	learn: 0.1262849	test: 0.1511652	best: 0.1511629 (919)	total: 26.1s	remaining: 2.24s
921:	learn: 0.1262531	test: 0.1511634	best: 0.1511629 (919)	total: 26.1s	remaining: 2.21s
922:	learn: 0.12

Выводы:
- one_hot_max_size = 12
- depth = 8+
- rsm = 0.5-
- random_strength - неважно

In [28]:
# готовим тюнинг гиперпараметров по сетке #2
model_grid_2 = CatBoostRegressor(iterations=1000, 
                               loss_function='MAE', 
                               eval_metric='MAPE',
                               one_hot_max_size=12,
                               logging_level='Silent')
grid_2 = {'depth': [8, 10, 12, 14, 16],
        'rsm': [0.3, 0.4, 0.5]
       }
# grid_search_result2 = model_grid_2.grid_search(grid_2,
#                                                full_pool,
#                                                cv=3,
#                                                plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	loss: 0.1481643	best: 0.1481643 (0)	total: 23.1s	remaining: 5m 24s
1:	loss: 0.1475185	best: 0.1475185 (1)	total: 50.1s	remaining: 5m 25s
2:	loss: 0.1525130	best: 0.1475185 (1)	total: 1m 40s	remaining: 6m 42s
3:	loss: 0.1513988	best: 0.1475185 (1)	total: 3m 48s	remaining: 10m 28s
4:	loss: 0.1570492	best: 0.1475185 (1)	total: 11m 2s	remaining: 22m 5s
5:	loss: 0.1481322	best: 0.1475185 (1)	total: 11m 32s	remaining: 17m 19s
6:	loss: 0.1475971	best: 0.1475185 (1)	total: 12m 6s	remaining: 13m 50s
7:	loss: 0.1503596	best: 0.1475185 (1)	total: 13m 9s	remaining: 11m 31s
8:	loss: 0.1532802	best: 0.1475185 (1)	total: 16m 5s	remaining: 10m 43s
9:	loss: 0.1557419	best: 0.1475185 (1)	total: 25m 8s	remaining: 12m 34s


KeyboardInterrupt: 

Выводы:
- one_hot_max_size = 12
- depth = 10+-
- rsm = 0.3-

In [29]:
# готовим тюнинг гиперпараметров по сетке #3
model_grid_3 = CatBoostRegressor(iterations=1000, 
                               loss_function='MAE', 
                               eval_metric='MAPE',
                               one_hot_max_size=12,
                               logging_level='Silent')
grid_3 = {'depth': [9, 10, 11],
        'rsm': [0.1, 0.2, 0.3]
       }
grid_search_result3 = model_grid_3.grid_search(grid_3,
                                               full_pool,
                                               cv=3,
                                               plot=True)

Custom logger is already specified. Specify more than one logger at same time is not thread safe.

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	loss: 0.1649576	best: 0.1649576 (0)	total: 10.5s	remaining: 1m 24s
1:	loss: 0.1636469	best: 0.1636469 (1)	total: 20.3s	remaining: 1m 10s
2:	loss: 0.1628797	best: 0.1628797 (2)	total: 30.3s	remaining: 1m
3:	loss: 0.1499856	best: 0.1499856 (3)	total: 52.9s	remaining: 1m 6s
4:	loss: 0.1516183	best: 0.1499856 (3)	total: 1m 13s	remaining: 59.2s
5:	loss: 0.1496554	best: 0.1496554 (5)	total: 1m 40s	remaining: 50.2s
6:	loss: 0.1473402	best: 0.1473402 (6)	total: 2m 10s	remaining: 37.4s
7:	loss: 0.1475185	best: 0.1473402 (6)	total: 2m 39s	remaining: 20s
8:	loss: 0.1477258	best: 0.1473402 (6)	total: 3m 17s	remaining: 0us
Estimating final quality...


Выводы:
- one_hot_max_size = 12
- depth = 9
- rsm = 0.3

In [21]:
# учим модель
# model = CatBoostRegressor(iterations=5000, 
#                           loss_function='MAE', 
#                           eval_metric='MAPE', 
#                           custom_metric='RMSE', 
#                           one_hot_max_size=4)
# model.fit(train_pool,
#           eval_set=valid_pool, 
#           logging_level='Silent', plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [14]:
# лучший результат
# display(model.get_best_score())
# число деревьев
# display(model.tree_count_)

{}

None

# Результат для Kaggle

In [30]:
X = pd.read_csv('EDAv2_Train.zip').drop(columns='price').drop(columns='description')
y = pd.read_csv('EDAv2_Train.zip', usecols=['price'])
display(X.shape, y.shape)
X_test = pd.read_csv('EDAv2_Test.zip').drop(columns='description')
y_test = pd.read_csv('sample_submission_empty.csv', usecols=['price']) # это пустой вектор, но нужен для полного обучения
display(X_test.shape, y_test.shape)

(86853, 16)

(86853, 1)

(34686, 16)

(34686, 1)

In [31]:
# оставим в тренировочном датасете только те бренды, которые есть в тестовом
brand_list = list(X_test['brand'].unique())
brand_mask = X['brand'].apply(lambda x: True if x in brand_list else False)
X = X[brand_mask]
y = y[brand_mask]
display(X.shape, y.shape)

(47453, 16)

(47453, 1)

In [32]:
# оставим в тренировочном датасете только б/у машины
used_cars_mask = list(X['n_owners'] != '0')
X = X[used_cars_mask]
y = y[used_cars_mask]
display(X.shape, y.shape)

(37841, 16)

(37841, 1)

In [33]:
# надо сделать одинаковый порядок фичей в train и test
# для этого сперва склеим их, а потом разделим
X['is_train'] = 1
X_test['is_train'] = 0
X_ = X.append(X_test)
X = X_[X_['is_train'] == 1].drop(columns=['is_train'])
X_test = X_[X_['is_train'] == 0].drop(columns=['is_train'])

In [34]:
# категориальные признаки
cat_features_list = ['body_type', 'brand', 'color', 'fuel_type', 'n_doors', 
                     'vehicle_transmission', 'drive_type', 'n_owners', 
                     'is_original_techpass', 'is_lefthand_drive', 'full_model_name']

In [35]:
display(X.columns)
display(X_test.columns)

Index(['body_type', 'brand', 'color', 'fuel_type', 'model_year', 'n_doors',
       'production_year', 'vehicle_transmission', 'engine_power', 'mileage',
       'drive_type', 'n_owners', 'is_original_techpass', 'is_lefthand_drive',
       'engine_displacement', 'full_model_name'],
      dtype='object')

Index(['body_type', 'brand', 'color', 'fuel_type', 'model_year', 'n_doors',
       'production_year', 'vehicle_transmission', 'engine_power', 'mileage',
       'drive_type', 'n_owners', 'is_original_techpass', 'is_lefthand_drive',
       'engine_displacement', 'full_model_name'],
      dtype='object')

In [36]:
# готовим для CatBoost
train_pool = Pool(X, y, cat_features=cat_features_list)
test_pool = Pool(X_test, y_test, cat_features=cat_features_list)

In [38]:
# учим модель
model = CatBoostRegressor(iterations=6000, 
                          loss_function='MAE', 
                          eval_metric='MAPE', 
                          custom_metric='RMSE',
                          one_hot_max_size=12,
                          depth=9,
                          rsm=0.3)
model.fit(train_pool,
          eval_set=test_pool,
          logging_level='Silent',
          plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [39]:
# лучший результат
display(model.get_best_score())
# число деревьев
display(model.tree_count_)

{'learn': {'MAE': 80702.0660804602,
  'MAPE': 0.08509110074875835,
  'RMSE': 346845.5540697369},
 'validation': {'MAE': 700407.4077409602,
  'MAPE': 700407.4077419598,
  'RMSE': 700625.6904303816}}

6000

In [40]:
# предсказываем результат
y_test_predict = model.predict(test_pool)

In [41]:
submission = pd.read_csv('sample_submission_empty.csv')
submission['price'] = y_test_predict
submission.to_csv('sample_submission_catboost_v2.csv', index=False)

In [43]:
# Тюнинг хорошо помог. До него был результат 15+, а стал 13+. Но всё равно хуже бэггинга.
# Сохраним модель для стекинга.
model.save_model('22_catboost_full_train.cbm')